<a href="https://colab.research.google.com/github/vitroid/cycless/blob/main/test.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
! pip install mdanalysis pairlist networkx py3Dmol cycless

     |████████████████████████████████| 19.6MB 1.3MB/s 
     |████████████████████████████████| 2.3MB 51.2MB/s 
     |████████████████████████████████| 2.0MB 50.9MB/s 
     |████████████████████████████████| 71kB 8.3MB/s 
     |████████████████████████████████| 337kB 51.6MB/s 
  Created wheel for mdanalysis: filename=MDAnalysis-1.0.0-cp36-cp36m-linux_x86_64.whl size=4553754 sha256=af21a90686a8daa02444fb2f735d08800861cf1ce24a8e0c4f1334f573e368c9
  Stored in directory: /root/.cache/pip/wheels/00/76/c9/b13be0d6f29176526e2062225904dab9c2a1f6bbcbe3a38bbc
  Created wheel for pairlist: filename=PairList-0.2.10.1-cp36-cp36m-linux_x86_64.whl size=34394 sha256=c2e7b6b0674e06628907cfe3178614707d1d15a37819f236c6bb7c0b8ba0af97
  Stored in directory: /root/.cache/pip/wheels/37/72/87/4f8910970c137259fe027866d3cf579d997bfdd52d5b0c5e5c
  Created wheel for methodtools: filename=methodtools-0.4.2-cp36-none-any.whl size=2987 sha256=bf68d9816ba1e2b1519e09f46643d2f88790a045d064a3d438d6849b60a2b46f
  Stored 

In [12]:
import MDAnalysis as mda
import pairlist
import numpy as np
import networkx as nx

def water_HB_digraph(waters, cellmat):
    dg = nx.DiGraph()
    celli   = np.linalg.inv(cellmat)
    H = np.array([u.atoms.positions[atom.index] for water in waters for atom in water.atoms if atom.name == "H"], dtype=float)
    O = np.array([u.atoms.positions[atom.index] for water in waters for atom in water.atoms if atom.name == "O"], dtype=float)
    # In a fractional coordinate
    rH = H @ celli
    rO = O @ celli
    # O-H distance is closer than 2.45 AA
    # Matsumoto JCP 2007 https://doi.org/10.1063/1.2431168
    for i,j,d in pairlist.pairs_iter(rH, 2.45, cellmat, pos2=rO):
        # but distance is greater than 1 AA (i.e. O and H are not in the same molecule)
        if 1 < d:
            # label of the molecule where Hydrogen i belongs.
            imol = i // 2
            # H to O vector
            # vec attribute is useful when you use cycless.dicycles.
            dg.add_edge(imol, j, vec=rO[j] - rH[i])
    return dg, rO


# Unfortunately, MDAnalysis does not read the concatenated gro file.
# https://docs.mdanalysis.org/stable/documentation_pages/coordinates/GRO.html
traj = open("/content/drive/MyDrive/npt_trjconv.gro")

u = mda.Universe(traj)
# cell dimension a,b,c,A,B,G
# Note: length unit of MDAnalysis is AA, not nm.
dimen   = u.trajectory.ts.dimensions
# cell matrix (might be transposed)
cellmat = mda.lib.mdamath.triclinic_vectors(dimen)
# Pick up water molecules only
waters = [residue for residue in u.residues if residue.resname[:3] == "SOL"]

# make a graph of hydrogen bonds and fractional coordinate of its vertices
dg, rO = water_HB_digraph(waters, cellmat)

# centering
rO -= 0.5 


/usr/local/lib/python3.6/dist-packages/MDAnalysis/topology/guessers.py:80: UserWarning: Failed to guess the mass for the following atom types: M
  warnings.warn("Failed to guess the mass for the following atom types: {}".format(atom_type))


Visualize the hydrogen-bond network.

In [50]:
import py3Dmol

def a2v3(a, labels="xyz"):
    return dict(zip(labels,a))

def Line(view,a,b,width=1.0):
    # https://3dmol.csb.pitt.edu/doc/$3Dmol.GLShape.html#addLine
    view.addLine({"start": a2v3(a),
                         "end":   a2v3(b),
                    # "color":"cyan",
                    })

def drawEdges(view, dg, rO, cellmat):
    for i,j in dg.edges():
        d = rO[j] - rO[i]
        d -= np.floor(d+0.5)
        a = rO[i] @ cellmat
        b = (rO[i]+d) @ cellmat
        Line(view, a, b)

view = py3Dmol.view()
drawEdges(view, dg, rO, cellmat)
view    

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Visualize the cycles (rings) in the network.

In [45]:
from cycless.cycles import cycles_iter, centerOfMass

def Polygon(view, vertices, color="black"):
    """
    vertices: np.array of positions of vertex of a cycle
    """
    center = np.average(vertices, axis=0)
    faces = [[0, i+1, i+2] for i in range(len(vertices))]
    faces[-1][2] = 1
    view.addCustom({"vertexArr": [a2v3(center)] + [a2v3(v) for v in vertices],
                    "faceArr": [x for f in faces for x in f],
                    "color": color,
                    }) 

def drawACycle(view, cycle, rO, cellmat, com=None, **kwarg):
    if com is None:
        com = centerOfMass(cycle, rO)
        com -= np.floor(com+0.5) 
    vertices = rO[cycle, :] - com
    vertices -= np.floor(vertices + 0.5)
    vertices = (vertices + com) @ cellmat
    Polygon(view, vertices, **kwarg)

def drawCycles(view, cycles, rO, cellmat, **kwarg):
    for cycle in cycles:
        drawACycle(view, cycle, rO, cellmat, **kwarg)

# undirected graph
g = nx.Graph(dg)
# detect the pentagons and hexagons.
cycles = [cycle for cycle in cycles_iter(g, maxsize=6, pos=rO) if len(cycle) > 4]
pentagons = [cycle for cycle in cycles if len(cycle) == 5]
hexagons = [cycle for cycle in cycles if len(cycle) == 6]
view = py3Dmol.view()
drawCycles(view, pentagons, rO, cellmat, color="red")
drawCycles(view, hexagons, rO, cellmat, color="green")
view

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Visualize the perfect cages.

In [51]:
from cycless.polyhed import polyhedra_iter

def drawAPolyhedron(view, poly, cycles, rO, cellmat, colors={5: "red", 6:"green"}):
    members = set([v for cid in poly for v in cycles[cid]])
    com = centerOfMass(list(members), rO)
    com -= np.floor(com+0.5)
    for cid in poly:
        drawACycle(view, cycles[cid], rO, cellmat, com=com, color=colors[len(cycles[cid])])


# detect the cages with number of faces between 12 and 16.
cages  = [cage for cage in polyhedra_iter(cycles, maxnfaces=16) if len(cage) > 11]
view = py3Dmol.view()
for cage in cages:
    drawAPolyhedron(view, cage, cycles, rO, cellmat)
drawEdges(view, dg, rO, cellmat)

view

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol